In [2]:
hdf5_data_path = '/scratch/ty296/hdf5_data/'
groupname = 'L'
p_fixed_name = 'p_ctrl'
p_fixed_value = 0.4
import os
print(os.getcwd())
import sys
sys.path.append('/scratch/ty296/CT_MPS_mini')
import h5py
import numpy as np

/scratch/ty296


In [3]:
# # statistical functions
# def mean_func(x):
#     return x.mean()

# def sem_func(x):
#     """Standard Error of Mean"""
#     return x.std() / np.sqrt(len(x))

# def variance_func(x):
#     return x.var()

# def sev_func(x):
#     """Standard Error of Variance"""
#     n = len(x)
#     if n <= 1:
#         return np.nan
#     # Standard error of variance formula
#     return x.var() * np.sqrt(2 / (n - 1))

In [4]:
# class data_processor:
#     def __init__(self, dir_name, n, threshold):
#         self.dir_name = dir_name
#         self.n = n
#         self.threshold = threshold
#         self.df_all_data = self.df_all_data()
    
#     def df_all_data(self):

#         def extract_tuples(hdf5_file_path, n, threshold):
#             all_data = []
#             single_file_data = read_hdf5_file(hdf5_file_path, load_sv_arrays=True)
#             for data_point_num in range(len(single_file_data)):
#                 L = single_file_data[data_point_num]['args']['L']
#                 p_ctrl = single_file_data[data_point_num]['p_ctrl']
#                 p_proj = single_file_data[data_point_num]['p_proj']
#                 s_0 = von_neumann_entropy_sv(single_file_data[data_point_num]['sv_arr'], n=n, positivedefinite=False, threshold=threshold)
#                 data_point = (L, p_ctrl, p_proj, s_0)
#                 all_data.append(data_point)
#             return all_data
        
#         df_all_data = pd.DataFrame()
#         # for file_num in tqdm.tqdm(range(len(os.listdir(dir_name)))):
#         for file_num in tqdm.tqdm(range(10)):
#             full_name = os.path.join(self.dir_name, list(os.listdir(self.dir_name))[file_num])
#             all_data = extract_tuples(full_name, n=self.n, threshold=self.threshold)
#             df = pd.DataFrame(all_data, columns=['L', 'p_ctrl', 'p_proj', 's_0'])
#             df_all_data = pd.concat([df_all_data, df])
#         return df_all_data

#     def plot(self):
#         # Simple plot
#         plt.figure(figsize=(10, 6))

#         # Get unique L values from df_all_data
#         L_values = sorted(self.df_all_data['L'].unique())
#         p_vary_label = 'p_proj'
#         p_fixed_label = 'p_ctrl' if p_vary_label == 'p_proj' else 'p_proj'
#         p_fixed_value = self.df_all_data[p_fixed_label].unique()[0]
#         y_label = 'Mean EE'
#         title = f'Mean EE vs p_proj ({p_fixed_label}={p_fixed_value})'
#         # Plot each L value
#         for L in L_values:
#             # Filter data for this L value
#             L_data = self.df_all_data.query(f'L == {L}')
            
#             # Group by p_proj and calculate mean and SEM
#             grouped = L_data.groupby(p_vary_label)['s_0'].agg([('mean', mean_func), ('sem', sem_func), ('variance', variance_func), ('sev', sev_func)]).reset_index()
#             # Plot mean with error bars
#             plt.errorbar(grouped[p_vary_label], 
#                         grouped['mean'], 
#                         yerr=grouped['sem'], 
#                         label=f'L={L}', marker='o')

#         plt.xlabel(p_vary_label)
#         plt.ylabel(y_label)
#         plt.title(title)
#         plt.legend()
#         plt.grid(True)
#         plt.savefig(f'/scratch/ty296/plots/s{self.n}_t{self.threshold}.png')
#         plt.show()

#     def save_plotting_data(self):
#         self.df_all_data.to_csv(f'/scratch/ty296/plots/s{self.n}_t{self.threshold}.csv')


In [5]:
# dir_name = '/scratch/ty296/hdf5_data/p_ctrl0.4'
# for threshold in np.logspace(-16, -5, 2):
#     data = data_processor(dir_name, n=0, threshold=threshold)
#     data.plot()
#     data.save_plotting_data()
# # result = df_all_data.groupby(['L', 'p_ctrl', 'p_proj'])['s_0'].agg([
# #     ('mean', mean_func),
# #     ('sem', sem_func), 
# #     ('variance', variance_func),
# #     ('sev', sev_func)
# # ])

In [6]:
# View singular values from your HDF5 file
filename = '/scratch/ty296/hdf5_data_combined/sv_combined_p_ctrl0.0.h5'
real_num = 0
with h5py.File(filename, 'r') as f:
    # Get the first key to examine
    first_key = list(f.keys())[real_num]
    print(f"Examining key: {first_key}")
    
    # Get the singular values array
    sv_array = f[first_key][()]
    
    # Display basic info
    print(f"Shape: {sv_array.shape}")
    print(f"Data type: {sv_array.dtype}")
    print(f"Number of singular values: {len(sv_array)}")
    
    # Display the actual values
    print(f"\nSingular values:")
    print(sv_array)
    
    # Display metadata
    print(f"\nMetadata:")
    for attr_name, attr_value in f[first_key].attrs.items():
        print(f"  {attr_name}: {attr_value}")


Examining key: real1
Shape: (1024,)
Data type: float64
Number of singular values: 1024

Singular values:
[6.23137332e-02 6.16276907e-02 6.14375849e-02 ... 1.48454760e-04
 1.22651931e-04 1.84403662e-05]

Metadata:
  L: 20
  maxbond: 1024
  maxdim: 1024
  n_chunk_realizations: 10
  p_ctrl: 0.0
  p_proj: 0.0
  seed: 8216


In [11]:
# Find all groups with L=24 and display their singular value arrays
filename = '/scratch/ty296/hdf5_data_combined/sv_combined_p_ctrl0.0.h5'

with h5py.File(filename, 'r') as f:
    L_target = 28
    matching_groups = []
    
    print(f"Searching for groups with L={L_target}...")
    print("=" * 80)
    
    # Loop through all realizations
    for key in f.keys():
        # Check if this group has L=24
        if 'L' in f[key].attrs and f[key].attrs['L'] == L_target:
            matching_groups.append(key)
    
    print(f"Found {len(matching_groups)} groups with L={L_target}")
    print()
    
    # Display information for each matching group
    for i, key in enumerate(matching_groups):
        sv_array = f[key][()]
        attrs = dict(f[key].attrs)
        
        print(f"Group {i+1}: {key}")
        print(f"  L = {attrs.get('L')}")
        print(f"  p_ctrl = {attrs.get('p_ctrl')}")
        print(f"  p_proj = {attrs.get('p_proj')}")
        print(f"  maxbond = {attrs.get('maxbond')}")
        print(f"  Singular value array shape: {sv_array.shape}")
        print(f"  Singular values: {sv_array}")
        print(f"  Max SV: {np.max(sv_array):.6e}")
        print(f"  Min SV: {np.min(sv_array):.6e}")
        print(f"  Number of SVs: {len(sv_array)}")
        print("-" * 60)


Searching for groups with L=28...
Found 20 groups with L=28

Group 1: real68280
  L = 28
  p_ctrl = 0.0
  p_proj = 1.0
  maxbond = 1
  Singular value array shape: (1,)
  Singular values: [1.]
  Max SV: 1.000000e+00
  Min SV: 1.000000e+00
  Number of SVs: 1
------------------------------------------------------------
Group 2: real68281
  L = 28
  p_ctrl = 0.0
  p_proj = 0.6210526315789474
  maxbond = 4
  Singular value array shape: (2,)
  Singular values: [0.91783422 0.3969639 ]
  Max SV: 9.178342e-01
  Min SV: 3.969639e-01
  Number of SVs: 2
------------------------------------------------------------
Group 3: real68282
  L = 28
  p_ctrl = 0.0
  p_proj = 0.5789473684210527
  maxbond = 2
  Singular value array shape: (1,)
  Singular values: [1.]
  Max SV: 1.000000e+00
  Min SV: 1.000000e+00
  Number of SVs: 1
------------------------------------------------------------
Group 4: real68283
  L = 28
  p_ctrl = 0.0
  p_proj = 0.5368421052631579
  maxbond = 2
  Singular value array shape: (2

In [8]:
# Plot singular values for all L=24 groups
L24_groups = []

with h5py.File(filename, 'r') as f:
    L_target = 24
    
    # Collect all L=24 groups
    for key in f.keys():
        if 'L' in f[key].attrs and f[key].attrs['L'] == L_target:
            L24_groups.append(key)


In [9]:
with h5py.File(filename, 'r') as f:
    for key in L24_groups:
        print(f[key].attrs.keys())
        print(f[key].attrs['p_proj'])

<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
1.0
<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
1.0
<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
0.6210526315789474
<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
0.5789473684210527
<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
0.5789473684210527
<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
0.5789473684210527
<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
0.5789473684210527
<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
0.5789473684210527
<KeysViewHDF5 ['L', 'maxbond', 'maxdim', 'n_chunk_realizations', 'p_ctrl', 'p_proj', 'seed']>
0.5789473684210527
<KeysViewHDF5

In [10]:
raw_data_path = "/scratch/ty296/hdf5_data/p_ctrl0.0/46312468_a0_L24.h5"

with h5py.File(raw_data_path, 'r') as f:
    # Top level structure
    print(f"Root keys: {list(f.keys())}")
    
    # Metadata group structure  
    metadata = f['metadata']
    print(f"Metadata groups: {len(metadata.keys())}")
    
    # Sample result structure
    sample = metadata['result_1']
    print(f"Sample result keys: {list(sample.keys())}")
    
    # Dataset lengths
    sv = f['singular_values']
    print(f"Singular values groups: {len(sv.keys())}")
    print(f"Sample SV shape: {sv['result_1'].shape}")
    

FileNotFoundError: [Errno 2] Unable to synchronously open file (unable to open file: name = '/scratch/ty296/hdf5_data/p_ctrl0.0/46312468_a0_L24.h5', errno = 2, error message = 'No such file or directory', flags = 0, o_flags = 0)

In [ ]:
30435/20

1521.75

In [ ]:
len(L24_groups)

200